In [1]:
from Functions import *
import Resources
import numpy as np

[[['00' '00' '00' ... '00' '00' '00']
  ['00' '00' '00' ... '00' '00' '00']]

 [['00' '00' '00' ... '00' '00' '00']
  ['00' '00' '00' ... '00' '00' '00']]

 [['00' '00' '00' ... '00' '00' '00']
  ['00' '00' '00' ... '00' '00' '00']]

 ...

 [['00' '00' '00' ... '00' '00' '00']
  ['00' '00' '00' ... '00' '00' '00']]

 [['00' '00' '00' ... '00' '00' '00']
  ['00' '00' '00' ... '00' '00' '00']]

 [['00' '00' '00' ... '00' '00' '00']
  ['00' '00' '00' ... '00' '00' '00']]]
running


In [2]:
# 加载器，将机器码程序加载到内存中
def loadProgram(file):
    fil = open(file,'r')
    lineno = 0
    address = np.int16(0)
    while True:
        line = fil.readline()
        lineno += 1
        if (lineno == 1 or lineno == 2):
            continue
        if(line == '' or line == '\n'):
            break
        try:
            instruc = line
            instruc = instruc.strip('\n')
            instruc = instruc.split(',')[0]
            instruc = instruc.split(';')[0]
            instruc = instruc.strip(',')    #指令为字符串类型,十六进制
            instruc = instruc.strip(';')

            print(instruc, len(instruc))
            
            for i in range(0, len(instruc)//2):
                Resources.Imem[address] = instruc[2*i : 2*i+2]
                address += 1
        except:
            print(f'File {file} line {lineno} has error')
            pass
    fil.close

In [3]:
loadProgram("test/test_speedup.coe")
print(Resources.Imem)
print(Resources.reg)
print(Resources.PC)

30F80100000000000000 20
30FB0100000000000000 20
30F90004000000000000 20
50010004000000000000 20
50310000000000000000 20
64B3 4
6030 4
40020004000000000000 20
6081 4
2012 4
6192 4
741E00000000000000 18
00 2
['30' 'F8' '01' ... '00' '00' '00']
[0, 0, 0, 0, 500, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
0


In [4]:
def check():
   #print(Resources.stat)
   if(Resources.stat == 1):
      return 1
   elif(Resources.stat == 2):
      print("Error: Halt")
      return 0
   elif(Resources.stat == 3):
      print("Error: ilegal address")
      return 0
   elif(Resources.stat == 4):
      print("Error: ilegal instruction")
      return 0

instruction_no = 0


In [5]:
import threading

# 下面这些是来自于上一个周期的信号，也就是这一周期各个阶段接受的输入信号
no = 0
# 控制信号，本周期末尾计算，在下个周期生效
IF_stall = 0
ID_stall = 0
EX_bubble = 0
IF_bubble = 0
##第一个参数：IF获取的拍数；第二个参数：EX执行所剩余的周期；第三个参数：EX是否在使用
EX_cycles = [0, 0]
# IF_ID寄存器的状态，即此时刻寄存器的值
IF_ID_status = (1, 0, 0, 0, 0, 0, 0)
# (pre_valP, pre_Cnd, pre_valC, IF_icode, EX_icode, MEM_icode, pre_valM, pre_PC)
IF_input_signals = (0, 0, 0, 1, 1, 1, 0, 0)

# (IF_icode, IF_ifun, IF_rA, IF_rB, IF_valP, IF_valC, IF_PC) 
ID_input_signals =(1, 0, 0, 0, 0, 0, 0)

# (ID_icode, ID_ifun, ID_valA, ID_valB, ID_valP, ID_valC, ID_rB, ID_rA, ID_dstE, ID_dstM) 
EX_input_signals = (1, 0, 0, 0, 0, 0, 0, 0, 15, 15)

# (EX_valE, EX_valP, EX_Cnd,  EX_valC, EX_icode, EX_ifun, EX_valA, EX_rB, EX_rA, EX_dstE, EX_dstM) 
MEM_input_signals = (0, 0, 0, 0, 1, 0, 0, 0, 0, 15, 15)

# (MEM_valP, MEM_Cnd, MEM_valC, MEM_icode, MEM_valM, MEM_rB, MEM_valE, MEM_ifun, MEM_rA, MEM_dstE, MEM_dstM)  
WB_input_signals = (0, 0, 0, 1, 0, 0, 0, 0, 0, 15, 15)

# ------------------------------------------------------------------------------------------------
# 下面是本周期计算完成产生的结果信号
# 这样分离是为了避免多线程带来的共享变量临界区

# (IF_icode, IF_ifun, IF_rA, IF_rB, IF_valP, IF_valC, IF_PC)
IF_result_signals = (1, 0, 15, 15, 0, 0, 0)

# (ID_icode, ID_ifun, ID_valA, ID_valB, ID_valP, ID_valC, ID_rB, ID_rA, ID_dstE, ID_dstM)
ID_result_signals =(1, 0, 0, 0, 0, 0, 15, 15, 15, 15)

# (EX_valE, EX_valP, EX_Cnd,  EX_valC, EX_icode, EX_ifun, EX_valA, EX_rB, EX_rA, EX_dstE, EX_dstM)
EX_result_signals = (0, 0, 0, 0, 1, 0, 0, 15, 15, 15, 15)

# (MEM_valP, MEM_Cnd, MEM_valC, MEM_icode, MEM_valM, MEM_rB, MEM_valE, MEM_ifun, MEM_rA, MEM_dstE, MEM_dstM)
MEM_result_signals = (0, 0, 0, 1, 0, 0, 0, 0, 15, 15, 15)

# (WB_icode, WB_ifun, WB_dstE, WB_dstM)
WB_result_signals = (0, 0, 15, 15)

In [6]:
# 五个阶段的线程任务函数
# 使用上一个周期的信号进行计算，产生本周期的输出信号
# 在后面的cycle函数中，一个周期的末尾，各个阶段都已经计算完成后，将上个周期的信号值更新为本周期计算产生的新的信号值
def task_fetch():
   global IF_input_signals, IF_result_signals, IF_stall, IF_bubble
   IF_result_signals = Fetch(IF_input_signals, IF_stall, IF_bubble)
   # TODO
   # 目前未考虑任何分支或者跳转指令
   # debug
   thread_id = threading.current_thread().name
   print(f"thread {thread_id} fetching")

def task_decode():
   global ID_input_signals, ID_result_signals
   ID_result_signals = Decode(ID_input_signals)
   # debug
   thread_id = threading.current_thread().name
   print(f"thread {thread_id} decoding")

def task_execute():
   global EX_input_signals, EX_result_signals
   EX_result_signals = Execute(EX_input_signals)
   # debug
   thread_id = threading.current_thread().name
   print(f"thread {thread_id} executing")

def task_memory():
   global MEM_input_signals, MEM_result_signals
   MEM_result_signals = Memory(MEM_input_signals)
   # debug
   thread_id = threading.current_thread().name
   print(f"thread {thread_id} memorying")

def task_writeback():
   global WB_input_signals, WB_result_signals
   WB_result_signals = WriteBack(WB_input_signals)
   # debug
   thread_id = threading.current_thread().name
   print(f"thread {thread_id} writingback")

In [7]:
execute = threading.Thread(target=task_execute)
# 模拟一个周期的执行，同一时刻五个阶段（线程）各自执行自己的指令
def cycle():
   # 本周期即将计算的信号和来自上一周期的计算完成的信号
   global IF_result_signals, ID_result_signals, EX_result_signals, MEM_result_signals
   global IF_input_signals, ID_input_signals, EX_input_signals, MEM_input_signals, WB_input_signals
   global IF_stall, ID_stall, EX_bubble, IF_ID_status, IF_bubble, EX_cycles, execute
   global no

   # 每个周期开始（模拟时钟上升沿）刷新控制信号和寄存器的值
   # 时钟上升沿更新各个阶段的输入信号的值
   (IF_icode, IF_ifun, IF_rA, IF_rB, IF_valP, IF_valC, IF_pc) = IF_result_signals
   MEM_valM = MEM_result_signals[4]
   EX_Cnd = EX_result_signals[2]
   EX_valC = EX_result_signals[3]
   EX_icode = EX_result_signals[4]
   MEM_icode = MEM_result_signals[3]
   # debug
   # print("EX_Cnd = ", EX_Cnd)
   # print("EX_valC = ", EX_valC)

   IF_input_signals = (IF_valP, EX_Cnd, EX_valC, IF_icode, EX_icode, MEM_icode, MEM_valM, IF_pc)

   # ID的输入来自IF_ID寄存器的输出
   (IF_ID_status, IF_ID_output) = IF_ID(IF_ID_status ,IF_result_signals, ID_stall)
   ID_input_signals = IF_ID_output

   # EX的输入来自ID_EX寄存器，EX没有被使用时
   if(EX_cycles[1] == 0):
      EX_input_signals = ID_EX(ID_result_signals, EX_bubble)

   MEM_input_signals = EX_result_signals
   WB_input_signals = MEM_result_signals


   # 创建5个线程，每个线程完成一个阶段的工作
   fetch = threading.Thread(target = task_fetch)
   decode = threading.Thread(target = task_decode) 
   # EX没有被使用，初始化EX
   if(EX_cycles[1] == 0):
      execute = threading.Thread(target=task_execute)
   memory = threading.Thread(target = task_memory)
   writeback = threading.Thread(target = task_writeback)

   fetch.start()
   decode.start()
   # EX没有被打开，打开EX同时设置EX剩余周期与打开的信号位
   if(EX_cycles[1] == 0):
      execute.start()
      EX_cycles[1] = 1
      if(EX_input_signals[0] == 6 and EX_input_signals[1] == 4):
         EX_cycles[0] = 5
      elif(EX_input_signals[0] == 6 and EX_input_signals[1] == 5):
         EX_cycles[0] = 10
      else:
         EX_cycles[0] = 1
   memory.start()
   writeback.start()

   # 每周期后1对EX还需执行周期减1
   if(EX_cycles[0] > 0):
      EX_cycles[0] -= 1

   fetch.join()
   decode.join()
   # EX执行剩余周期为0，且EX还在被使用，释放EX
   if(EX_cycles[0] == 0 and EX_cycles[1] == 1):
      execute.join()
      EX_cycles[1] = 0
   memory.join()
   writeback.join()

   ID_rA = ID_result_signals[7]; ID_rB = ID_result_signals[6];
   EX_dstM = EX_result_signals[10]; EX_dstE = EX_result_signals[9]

   IF_icode = IF_result_signals[0]; ID_icode = ID_result_signals[0]; EX_icode = EX_result_signals[4];

   MEM_dstM = MEM_result_signals[10]; MEM_dstE = MEM_result_signals[9]
   WB_dstM = WB_result_signals[3]; WB_dstE = WB_result_signals[2]

   # 在周期末尾更新控制信号,控制信号在下一个周期生效
   HD_signals = (ID_rA, ID_rB, EX_dstM, EX_dstE, MEM_dstM, MEM_dstE, WB_dstM, WB_dstE, IF_icode, ID_icode, EX_icode, EX_cycles[0])
   # print("(ID_rA, ID_rB, EX_dstM, EX_dstE, MEM_dstM, MEM_dstE, WB_dstM, WB_dstE, IF_icode, ID_icode, EX_icode, EX_cycles[0]):",HD_signals)
   (ID_stall, EX_bubble, IF_stall, IF_bubble) = Hazard_Detection(HD_signals)
   # debug
   # print("(ID_stall, EX_bubble, IF_stall, IF_bubble) = ",(ID_stall, EX_bubble, IF_stall, IF_bubble))

   if check() == False:
      return False

   # debug
   # print(Resources.reg)
   # print("Resources.ZF = ",Resources.ZF)

   return True

In [8]:
while True:
    if not cycle():
        break
    print(f"current cycle:{no}")
    no += 1
    print()

# print(Resources.mem)
print(Resources.reg)

thread Thread-6 fetching
thread Thread-7 decoding
thread Thread-8 executing
thread Thread-9 memorying
thread Thread-10 writingback
current cycle:0

thread Thread-11 fetching
thread Thread-12 decoding
thread Thread-13 executing
thread Thread-14 memorying
thread Thread-15 writingback
current cycle:1

thread Thread-16 fetching
thread Thread-17 decoding
thread Thread-18 executing
thread Thread-19 memorying
thread Thread-20 writingback
current cycle:2

thread Thread-21 fetching
thread Thread-22 decoding
thread Thread-23 executing
thread Thread-24 memorying
thread Thread-25 writingback
current cycle:3

thread Thread-26 fetching
thread Thread-27 decoding
thread Thread-28 executing
thread Thread-29 memorying
thread Thread-30 writingback
current cycle:4

thread Thread-31 fetching
thread Thread-32 decoding
thread Thread-33 executing
thread Thread-34 memorying
thread Thread-35 writingback
current cycle:5

thread Thread-36 fetching
thread Thread-37 decoding
thread Thread-38 executing


Exception in thread Thread-39:
Traceback (most recent call last):
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 917, in run
    self._target(*self._args, **self._kwargs)
  File "C:\Users\mangp\AppData\Local\Temp\ipykernel_25692\3905627679.py", line 29, in task_memory
  File "c:\Users\mangp\Desktop\programs\体系结构\Y86-64-simulator\Functions.py", line 373, in Memory
    MEM_valM = hex_2_dec(Load_Data_Memory(EX_valE, 8))
  File "c:\Users\mangp\Desktop\programs\体系结构\Y86-64-simulator\Functions.py", line 21, in Load_Data_Memory
    a += Resources.L1_Cache.Read_Cache(address + i)
UnboundLocalError: local variable 'a' referenced before assignment
Exception in thread Thread-44:
Traceback (most recent call last):
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 9

thread Thread-40 writingback
current cycle:6

thread Thread-41 fetching
thread Thread-42 decoding
thread Thread-43 executing
thread Thread-45 writingback
current cycle:7

thread Thread-46 fetching
thread Thread-47 decoding
thread Thread-48 executing
thread Thread-49 memorying
thread Thread-50 writingback
current cycle:8

thread Thread-51 fetching
thread Thread-52 decoding
thread Thread-53 memorying
thread Thread-54 writingback
current cycle:9

thread Thread-55 fetching
thread Thread-56 decoding
thread Thread-57 memorying
thread Thread-58 writingback
current cycle:10

thread Thread-59 fetching
thread Thread-60 decoding
thread Thread-61 memorying
thread Thread-62 writingback
current cycle:11

thread Thread-63 fetching
thread Thread-64 decoding
thread Thread-65 memorying
thread Thread-66 writingback
current cycle:12

thread Thread-67 fetching
thread Thread-68 decoding
thread Thread-69 executing
thread Thread-70 memorying
thread Thread-71 writingback
current cycle:13

thread Thread-72 fetc

Exception in thread Thread-110:
Traceback (most recent call last):
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 917, in run
    self._target(*self._args, **self._kwargs)
  File "C:\Users\mangp\AppData\Local\Temp\ipykernel_25692\3905627679.py", line 29, in task_memory
  File "c:\Users\mangp\Desktop\programs\体系结构\Y86-64-simulator\Functions.py", line 370, in Memory
    Store_Data_Memory(EX_valE, 8, EX_valA)
TypeError: Store_Data_Memory() takes 2 positional arguments but 3 were given


Exception in thread Thread-175:
Traceback (most recent call last):
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 917, in run
    self._target(*self._args, **self._kwargs)
  File "C:\Users\mangp\AppData\Local\Temp\ipykernel_25692\3905627679.py", line 29, in task_memory
  File "c:\Users\mangp\Desktop\programs\体系结构\Y86-64-simulator\Functions.py", line 373, in Memory
    MEM_valM = hex_2_dec(Load_Data_Memory(EX_valE, 8))
  File "c:\Users\mangp\Desktop\programs\体系结构\Y86-64-simulator\Functions.py", line 21, in Load_Data_Memory
    a += Resources.L1_Cache.Read_Cache(address + i)
UnboundLocalError: local variable 'a' referenced before assignment
Exception in thread Thread-180:
Traceback (most recent call last):
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line

...

Exception in thread Thread-129924:
Traceback (most recent call last):
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 917, in run
    self._target(*self._args, **self._kwargs)
  File "C:\Users\mangp\AppData\Local\Temp\ipykernel_25692\3905627679.py", line 29, in task_memory
  File "c:\Users\mangp\Desktop\programs\体系结构\Y86-64-simulator\Functions.py", line 373, in Memory
    MEM_valM = hex_2_dec(Load_Data_Memory(EX_valE, 8))
  File "c:\Users\mangp\Desktop\programs\体系结构\Y86-64-simulator\Functions.py", line 21, in Load_Data_Memory
    a += Resources.L1_Cache.Read_Cache(address + i)
UnboundLocalError: local variable 'a' referenced before assignment
Exception in thread Thread-129990:
Traceback (most recent call last):
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py"

current cycle:26746

thread Thread-129921 fetching
thread Thread-129922 decoding
thread Thread-129923 executing
thread Thread-129925 writingback
current cycle:26747

thread Thread-129926 fetching
thread Thread-129927 decoding
thread Thread-129928 executing
thread Thread-129929 memorying
thread Thread-129930 writingback
current cycle:26748

thread Thread-129931 fetching
thread Thread-129932 decoding
thread Thread-129933 memorying
thread Thread-129934 writingback
current cycle:26749

thread Thread-129935 fetching
thread Thread-129936 decoding
thread Thread-129937 memorying
thread Thread-129938 writingback
current cycle:26750

thread Thread-129939 fetching
thread Thread-129940 decoding
thread Thread-129941 memorying
thread Thread-129942 writingback
current cycle:26751

thread Thread-129943 fetching
thread Thread-129944 decoding
thread Thread-129945 memorying
thread Thread-129946 writingback
current cycle:26752

thread Thread-129947 fetching
thread Thread-129948 decoding
thread Thread-1299

Exception in thread Thread-130599:
Traceback (most recent call last):
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 980, in _bootstrap_inner
    self.run()
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py", line 917, in run
    self._target(*self._args, **self._kwargs)
  File "C:\Users\mangp\AppData\Local\Temp\ipykernel_25692\3905627679.py", line 29, in task_memory
  File "c:\Users\mangp\Desktop\programs\体系结构\Y86-64-simulator\Functions.py", line 373, in Memory
    MEM_valM = hex_2_dec(Load_Data_Memory(EX_valE, 8))
  File "c:\Users\mangp\Desktop\programs\体系结构\Y86-64-simulator\Functions.py", line 21, in Load_Data_Memory
    a += Resources.L1_Cache.Read_Cache(address + i)
UnboundLocalError: local variable 'a' referenced before assignment
Exception in thread Thread-130604:
Traceback (most recent call last):
  File "e:\Program Files (x86)\Microsoft Visual Studio\Shared\Python39_64\lib\threading.py"

thread Thread-130600 writingback
current cycle:26886

thread Thread-130601 fetching
thread Thread-130602 decoding
thread Thread-130603 executing
thread Thread-130605 writingback
current cycle:26887

thread Thread-130606 fetching
thread Thread-130607 decoding
thread Thread-130608 executing
thread Thread-130609 memorying
thread Thread-130610 writingback
current cycle:26888

thread Thread-130611 fetching
thread Thread-130612 decoding
thread Thread-130613 memorying
thread Thread-130614 writingback
current cycle:26889

thread Thread-130615 fetching
thread Thread-130616 decoding
thread Thread-130617 memorying
thread Thread-130618 writingback
current cycle:26890

thread Thread-130619 fetching
thread Thread-130620 decoding
thread Thread-130621 memorying
thread Thread-130622 writingback
current cycle:26891

thread Thread-130623 fetching
thread Thread-130624 decoding
thread Thread-130625 memorying
thread Thread-130626 writingback
current cycle:26892

thread Thread-130627 fetching
thread Thread-1

KeyboardInterrupt: 